In [1]:
from ast import literal_eval
import pandas as pd
import numpy as np
import warnings
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
warnings.filterwarnings(action='ignore')
import warnings
warnings.filterwarnings('ignore')

import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.cluster import KMeans, MiniBatchKMeans
from scipy.spatial.distance import euclidean
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import MinMaxScaler

In [74]:
evaldict=dict()

In [3]:
datadf=pd.read_csv('./data/책영화리스트_8183.csv')
newdf=pd.read_csv('./data/pivot_all.csv')
df=pd.read_csv('./data/cluster_total.csv')
bookdf = df[df['content']=='b']
moviedf = df[df['content']=='m']

In [4]:
newdf=newdf.iloc[1:]
newdf.fillna(0)

Unnamed: 0              userid 24BqEWE785rjn  2mwvg7EagvMa7  \
1               1  b10 1/2장으로 쓴 세계 역사             0            0.0   
2               2         b1001개의 거짓말             0            0.0   
3               3                b11분             0            3.0   
4               4              b13.67             0            0.0   
5               5               b13계단             0            0.0   
...           ...                 ...           ...            ...   
66105       66105              mU-571             0            0.0   
66106       66106            mUFO 스케치             0            0.0   
66107       66107     mX 파일 - 미래와의 전쟁             0            0.0   
66108       66108           mYMCA 야구단             0            0.0   
66109       66109                 총합계        3741.5         2971.0   

       2mwvgaAjwxMa7  2mwvgbGLgqMa7  2mwvggAE2vMa7  2mwvgLpo25Ma7  \
1                0.0            0.0            0.0            0.0   
2                0.0            0.0            0.0            0.0   
3                3.5            0.0            0.0            3.5   
4                0.0            0.0            0.0            0.0   
5                0.0            0.0            0.0            0.0   
...              ...            ...            ...            ...   
66105            2.5            0.0            0.0            0.0   
66106            0.0            0.0            0.0            0.0   
66107            0.0            0.0            0.0            0.0   
66108            0.0            0.0            0.0            0.0   
66109         4422.0         2526.0         3148.5         7436.5   

       2mwvgYmarxMa7  36lvX3jzZqXdn  ...  ZBm5RVn735d46  zNM5N1gz7v26j  \
1                0.0            0.0  ...            0.0            0.0   
2                0.0            0.0  ...            0.0            0.0   
3                4.5            0.0  ...            0.0            0.0   
4                4.0            0.0  ...            0.0            0.0   
5                3.5            0.0  ...            0.0            0.0   
...              ...            ...  ...            ...            ...   
66105            0.0            3.5  ...            0.0            0.0   
66106            0.0            0.0  ...            0.0            0.0   
66107            0.0            3.0  ...            0.0            0.0   
66108            0.0            0.0  ...            0.0            0.0   
66109         3954.0         3333.5  ...         2476.0         1472.0   

       zNM5NARwPGv26  ZWpqMaWa1qrkn  ZWpqMMERlqrkn       총합계  \
1                0.0            0.0            0.0       4.0   
2                0.0            0.0            0.0       3.5   
3                0.0            0.0            0.0      77.0   
4                0.0            0.0            0.0      42.5   
5                0.0            0.0            0.0      33.5   
...              ...            ...            ...       ...   
66105            0.0            0.0            0.0      23.0   
66106            0.0            0.0            0.0       2.0   
66107            0.0            0.0            0.0      10.5   
66108            0.0            0.0            0.0      31.5   
66109          603.5          849.0         2196.0  286317.5   

                    title  rating  vote_count  content  
1      b10 1/2장으로 쓴 세계 역사     4.0         1.0        b  
2             b1001개의 거짓말     3.5         1.0        b  
3                    b11분     3.5        22.0        b  
4                  b13.67     3.9        11.0        b  
5                   b13계단     3.7         9.0        b  
...                   ...     ...         ...      ...  
66105              mU-571     2.9         8.0        m  
66106            mUFO 스케치     2.0         1.0        m  
66107     mX 파일 - 미래와의 전쟁     3.5         3.0        m  
66108           mYMCA 야구단     2.9        11.0        m  
66109                   0     0.0         0.0       

In [5]:
users=newdf.iloc[0][2:-5].keys()

In [8]:
len(users)

111

In [9]:
users

Index(['24BqEWE785rjn', '2mwvg7EagvMa7', '2mwvgaAjwxMa7', '2mwvgbGLgqMa7',
       '2mwvggAE2vMa7', '2mwvgLpo25Ma7', '2mwvgYmarxMa7', '36lvX3jzZqXdn',
       '36lvXmWQZ5Xdn', '3BnvwpKaj5PAY',
       ...
       'YMKqmLrErxloD', 'YMKqmne6Pkvlo', 'YMKqmwrVr5loD', 'ZBm5Rgkl9xd46',
       'ZBm5RNnk95d46', 'ZBm5RVn735d46', 'zNM5N1gz7v26j', 'zNM5NARwPGv26',
       'ZWpqMaWa1qrkn', 'ZWpqMMERlqrkn'],
      dtype='object', length=111)

In [10]:
len(datadf)

8187

In [11]:
del datadf['Unnamed: 0']

In [12]:
datadf.columns=['title','plot']

In [13]:
datadf = datadf[datadf['plot'].notnull()].reset_index(drop=True)
datadf.shape

(8183, 2)

# 코사인으로 쭉


## 코사인유사도

In [14]:
from sklearn.feature_extraction.text import TfidfVectorizer
vect = TfidfVectorizer()

In [15]:
tfidf = TfidfVectorizer(stop_words='english')

In [16]:
tfidf_matrix = tfidf.fit_transform(datadf['plot'])
print(tfidf_matrix.shape)

(8183, 163167)


In [17]:
from sklearn.metrics.pairwise import cosine_similarity
cosine_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)


In [18]:
np.round(cosine_matrix, 4)

array([[1.    , 0.0028, 0.0019, ..., 0.005 , 0.0021, 0.0017],
       [0.0028, 1.    , 0.0141, ..., 0.0201, 0.0104, 0.0026],
       [0.0019, 0.0141, 1.    , ..., 0.    , 0.    , 0.0021],
       ...,
       [0.005 , 0.0201, 0.    , ..., 1.    , 0.0452, 0.006 ],
       [0.0021, 0.0104, 0.    , ..., 0.0452, 1.    , 0.0154],
       [0.0017, 0.0026, 0.0021, ..., 0.006 , 0.0154, 1.    ]])

In [19]:
datadf.drop_duplicates(keep='first', inplace=True)

In [20]:
datadf.columns=['title','plot']

In [21]:
# movie title와 id를 매핑할 dictionary를 생성해줍니다. 
title2id = {}
for i, c in enumerate(datadf['title']): title2id[i] = c

# id와 movie title를 매핑할 dictionary를 생성해줍니다. 
id2title = {}
for i, c in title2id.items(): id2title[c] = i

In [22]:
len(title2id)

8183

In [23]:
df=datadf

In [24]:
goal='m쇼생크 탈출'
idx = id2title[goal]
goalcate=goal[0]

In [25]:
df.loc[df['title'] ==goal]

title                                               plot
1347  m쇼생크 탈출  촉망 받던 은행 부지점장 ‘ 팀 로빈슨   아내와 그 애인을 살해한 혐의로 종신형을...

In [26]:
same_sim_scores=[]
for i,c in enumerate(cosine_matrix[idx]):
    if title2id[i][0] ==goalcate and i !=idx:
        same_sim_scores.append((i,c))

In [27]:
diff_sim_scores=[]
for i,c in enumerate(cosine_matrix[idx]):
    if title2id[i][0]!=goalcate:
        diff_sim_scores.append((i,c))

In [28]:
same_sim_scores = sorted(same_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
diff_sim_scores = sorted(diff_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
same_result = [(title2id[i], score) for i, score in same_sim_scores]
diff_result=[(title2id[i], score) for i, score in diff_sim_scores]
same_result=pd.DataFrame(same_result)
diff_result=pd.DataFrame(diff_result)
same_result.columns=['title','similarity']
diff_result.columns=['title','similarity']
result=pd.concat([same_result,diff_result],axis=1)

In [29]:
result

title  similarity          title  similarity
0           m스틸워터    0.124372             b포    0.031878
1         m언디스퓨티드    0.119381      b좀머 씨 이야기    0.021789
2           m프리즈너    0.096173            b중용    0.021454
3            m빠삐용    0.078903        b파이트 클럽    0.020542
4            m화소도    0.067250          b경성기담    0.019365
5          m스타드 업    0.065875       b시민의 불복종    0.018303
6        m7번방의 선물    0.065400  b방드르디, 태평양의 끝    0.016091
7     m시저는 죽어야 한다    0.063457   b우리들의 행복한 시간    0.015527
8          m신북두신권    0.060560            b속죄    0.015526
9       m집으로 가는 길    0.057356          b13계단    0.015361
10       m친절한 금자씨    0.051117            b강의    0.015152
11           m프리즌    0.050903            b질투    0.014126
12           m컨빅션    0.050875          b가시고기    0.012995
13  m잭 리처: 네버 고 백    0.049506    b미드나잇 라이브러리    0.012988
14        m인디안 썸머    0.047713       b걸리버 여행기    0.012370

In [28]:
class cross_recommendation_cluster:
    def __init__(self, **kargs):
        self.topn = kargs.get('topn', 20)
        self.df = kargs.get('data', pd.read_csv(fname))
        self.a, self.b, self.c = kargs.get('a',0.9), kargs.get('b',0.05), kargs.get('c',0.05)
        self.n_clusters = kargs.get('n_clusters',30)# kmeans
        self.n_components = kargs.get('n_components', 90)# svd
        self.vote_thres = kargs.get('vote_thres',1)# vote_count
        self.verbose = kargs.get('verbose', 1)
        self.re_cluster = kargs.get('re_cluster', 1)# kmeans
        self.batch_size = kargs.get('batch_size', 2000)
        self.max_iter = kargs.get('max_iter', 500)
        
        self.cvec = CountVectorizer(min_df=0, ngram_range=(1,2))
        self.stops = []
        with open('./stopwords/total_stopwords', encoding='utf-8') as f:
            self.stops.append(f.readline()[:-2])
        
        if self.verbose == 1:
            print('-'*35)
            print('# Parameters')
            print('      a, b, c        : {0}, {1}, {2}'.format(self.a, self.b, self.c))
            print('vote count threshold :', self.vote_thres)
            print("n_components of SVD  :", self.n_components)
            print("n_clusters of KMeans :", self.n_clusters)
            print('batch_size of Kmeans :', self.batch_size)
            print('max_iter of Kmeans   :', self.max_iter)
            print('weighted_sum = dist_scaled*{0}(a) + genre_scaled*{1}(b) + wvote_scaled*{2}(c)'.format(self.a, self.b, self.c))
            print('-'*35)
    
    def search_title(self, title_name):
        return self.df[self.df['title'].str.contains(title_name)].title
    
    def genre_sim_sorted(self, title_idx):
        genre_literal = self.df['genre'].apply(lambda x: x.replace('|',' '))
        genre = self.cvec.fit_transform(genre_literal)
        genre_sim = cosine_similarity(genre,genre)
        
        return np.array([(idx,sim) for idx,sim in enumerate(genre_sim[title_idx])])
    
    def raw_to_tfidf(self, data_preprocess):
        tfidf = TfidfVectorizer(analyzer='word', ngram_range=(1,3),stop_words=self.stops,
                                     min_df=3, max_df=0.95, max_features=10000)
        return tfidf.fit_transform(data_preprocess)
    def tfidf_to_svd(self, data_tfidf):
        svd = TruncatedSVD(n_components=self.n_components, n_iter=10)
        return svd.fit_transform(data_tfidf)
    
    def similar_cluster_movies(self, title_idx):
        do_cluster, loop_cnt = True, 0
        
        # data preprocessing
#         data_tfidf = self.raw_to_tfidf(list(map(str, self.df['plot_preprocessed_kkma'].values)))
        data_tfidf = self.raw_to_tfidf(list(map(str, self.df['plot_preprocessed_kkma'].values)))

        data_svd = self.tfidf_to_svd(data_tfidf)
        
        # K-means clustering
        print('Clustering...')
        while do_cluster:
            kmeans = MiniBatchKMeans(n_clusters=self.n_clusters, batch_size=self.batch_size,
                                     max_iter=self.max_iter, verbose=0 ,n_init=3)

            vote_over_thres_idx = self.df[self.df['vote_count'] > self.vote_thres].index
            data_svd_idx = np.array([(idx,val) for idx,val in zip(self.df.index,data_svd)])
            data_svd_to_km = [val for idx,val in data_svd_idx if idx in vote_over_thres_idx]
            data_svd_dict = dict([(idx,val) for idx,val in filter(lambda x: x[0] in vote_over_thres_idx, data_svd_idx)])
            
            # (optional)avoid biggest cluster
            km = kmeans.fit(data_svd_to_km)
            km_dict = dict([(df_idx,label_) for df_idx,label_ in zip(vote_over_thres_idx,km.labels_)])
            km_cluster = list(filter(lambda x: km_dict.get(x) == km_dict.get(title_idx), km_dict.keys()))

            clusters = [0]*self.n_clusters
            for label_ in km.labels_:
                clusters[label_] += 1

            clusters_idx = np.array(clusters).argsort()
            bad_clusters = clusters_idx[-3:]
            
            if self.re_cluster:            
                if km_dict.get(title_idx) not in bad_clusters:
                    do_cluster=False
                elif loop_cnt >= 20:
                    print('Loop count exceeded')
                    do_cluster=False
                else:
                    del kmeans
                    loop_cnt += 1
                    print('Re-clustering...(%d)'%(loop_cnt))
                    
            else:
                do_cluster = False

        if self.verbose == 1:
            print('-'*35)
            print('# K-means clustering distribution')
            for i,size in enumerate(clusters):
                postfix = '<==' if i == km_dict.get(title_idx) else ''
                print('cluster #%3d : %4d items %s'%(i,size,postfix))
            print('-'*35)
        closest=[]

        try:
            for i in km_cluster:
                if i != title_idx:
                    closest.append((i,euclidean(data_svd_dict.get(title_idx), data_svd_dict.get(i))))
            return np.array(closest), self.df.loc[np.array(sorted(closest, key=lambda x: x[1]))[:,0]]

        except:     
            closest=(([(0,0)]))
            
            return np.array(closest), self.df.loc[np.array(sorted(closest, key=lambda x: x[1]))[:,0]]

    def result_by_weights(self, dataf):
        dataf['weighted_sum'] = dataf['dist_scaled']*self.a + dataf['genre_scaled']*self.b + dataf['wvote_scaled']*self.c
        
        return dataf.sort_values('weighted_sum', ascending=False)

            
    def getMovies(self, title):
        # no title result
        try: title_idx = self.df[self.df['title']== title].index.values[0]
        except:
            raise ValueError('There is no such title name. Search with "search_title" function')
        
        # get movies in same cluster
        dist, result = self.similar_cluster_movies(title_idx)
        
        # merge with distance
        result = pd.merge(result, pd.Series(dist[:,1], name='dist'), left_on=result.index, right_on=dist[:,0])
        result.rename(columns={'key_0':'idx'}, inplace=True)
        
        # IMDB's weighted_vote
        def weighted_vote_average(record):
            v, r = record['vote_count'], record['rating']
            return (v/(v+m))*r + (m/(m+v))*c
        c = result['rating'].mean()
        m = result['vote_count'].quantile(.6)
        result['weighted_vote'] = result.apply(weighted_vote_average,axis=1)
        
        # merge with genre
        genre_sim = self.genre_sim_sorted(title_idx)
        result_with_genre = pd.merge(result, pd.Series(genre_sim[:,1], name='genre_sim'), left_on=result.idx, right_on=genre_sim[:,0],)
        
        # minmax scale
        result_with_genre['wvote_scaled'] = MinMaxScaler().fit_transform(result_with_genre['weighted_vote'].values.reshape(-1,1))
        result_with_genre['genre_scaled'] = MinMaxScaler().fit_transform(result_with_genre['genre_sim'].values.reshape(-1,1))
        result_with_genre['dist_scaled'] = MinMaxScaler().fit_transform(result_with_genre['dist'].max() - result_with_genre['dist'].values.reshape(-1,1))
        
        # (optional)remove data with 0 genre score
        no_genre_score_idx = result_with_genre[result_with_genre['genre_sim'] == 0].index
        result_with_genre.drop(no_genre_score_idx, inplace=True)
        
        result_with_genre = self.result_by_weights(result_with_genre)
        return result_with_genre.head(self.topn)

In [29]:
class book_recommendation_cluster:
    def __init__(self, **kargs):
        self.topn = kargs.get('topn', 20)
        self.df = kargs.get('data', pd.read_csv('./data/cluster_book.csv'))
        self.a, self.b, self.c = kargs.get('a',0.9), kargs.get('b',0), kargs.get('c',0.1)
        self.n_clusters = kargs.get('n_clusters',30)# kmeans
        self.n_components = kargs.get('n_components', 90)# svd
        self.vote_thres = kargs.get('vote_thres',1)# vote_count
        self.verbose = kargs.get('verbose', 1)
        self.re_cluster = kargs.get('re_cluster', 1)# kmeans
        self.batch_size = kargs.get('batch_size', 2000)
        self.max_iter = kargs.get('max_iter', 500)
        
        self.cvec = CountVectorizer(min_df=0, ngram_range=(1,2))
        self.stops = []
        with open('./stopwords/total_stopwords', encoding='utf-8') as f:
            self.stops.append(f.readline()[:-2])
        
        if self.verbose == 1:
            print('-'*35)
            print('# Parameters')
            print('      a, b, c        : {0}, {1}, {2}'.format(self.a, self.b, self.c))
            print('vote count threshold :', self.vote_thres)
            print("n_components of SVD  :", self.n_components)
            print("n_clusters of KMeans :", self.n_clusters)
            print('batch_size of Kmeans :', self.batch_size)
            print('max_iter of Kmeans   :', self.max_iter)
            print('weighted_sum = dist_scaled*{0}(a) + genre_scaled*{1}(b) + wvote_scaled*{2}(c)'.format(self.a, self.b, self.c))
            print('-'*35)
    
    def search_title(self, title_name):
        return self.df[self.df['title'].str.contains(title_name)].title
    
    def genre_sim_sorted(self, title_idx):
        genre_literal = self.df['genre'].apply(lambda x: x.replace('|',' '))
        genre = self.cvec.fit_transform(genre_literal)
        genre_sim = cosine_similarity(genre,genre)
        
        return np.array([(idx,sim) for idx,sim in enumerate(genre_sim[title_idx])])
    
    def raw_to_tfidf(self, data_preprocess):
        tfidf = TfidfVectorizer(analyzer='word', ngram_range=(1,3),stop_words=self.stops,
                                     min_df=3, max_df=0.95, max_features=10000)
        return tfidf.fit_transform(data_preprocess)
    def tfidf_to_svd(self, data_tfidf):
        svd = TruncatedSVD(n_components=self.n_components, n_iter=10)
        return svd.fit_transform(data_tfidf)
    
    def similar_cluster_movies(self, title_idx):
        do_cluster, loop_cnt = True, 0
        
        # data preprocessing
        data_tfidf = self.raw_to_tfidf(list(map(str, self.df['plot'].values)))
        data_svd = self.tfidf_to_svd(data_tfidf)
        
        # K-means clustering
        print('Clustering...')
        while do_cluster:
            kmeans = MiniBatchKMeans(n_clusters=self.n_clusters, batch_size=self.batch_size,
                                     max_iter=self.max_iter, verbose=0 ,n_init=3)

            vote_over_thres_idx = self.df[self.df['vote_count'] > self.vote_thres].index
            data_svd_idx = np.array([(idx,val) for idx,val in zip(self.df.index,data_svd)])
            data_svd_to_km = [val for idx,val in data_svd_idx if idx in vote_over_thres_idx]
            data_svd_dict = dict([(idx,val) for idx,val in filter(lambda x: x[0] in vote_over_thres_idx, data_svd_idx)])
            
            # (optional)avoid biggest cluster
            km = kmeans.fit(data_svd_to_km)
            km_dict = dict([(df_idx,label_) for df_idx,label_ in zip(vote_over_thres_idx,km.labels_)])
            km_cluster = list(filter(lambda x: km_dict.get(x) == km_dict.get(title_idx), km_dict.keys()))

            clusters = [0]*self.n_clusters
            for label_ in km.labels_:
                clusters[label_] += 1

            clusters_idx = np.array(clusters).argsort()
            bad_clusters = clusters_idx[-3:]
            
            if self.re_cluster:            
                if km_dict.get(title_idx) not in bad_clusters:
                    do_cluster=False
                elif loop_cnt >= 20:
                    print('Loop count exceeded')
                    do_cluster=False
                else:
                    del kmeans
                    loop_cnt += 1
                    print('Re-clustering...(%d)'%(loop_cnt))
                    
            else:
                do_cluster = False

        if self.verbose == 1:
            print('-'*35)
            print('# K-means clustering distribution')
            for i,size in enumerate(clusters):
                postfix = '<==' if i == km_dict.get(title_idx) else ''
                print('cluster #%3d : %4d items %s'%(i,size,postfix))
            print('-'*35)

        closest = []
        try:
            for i in km_cluster:
                if i != title_idx:
                    closest.append((i,euclidean(data_svd_dict.get(title_idx), data_svd_dict.get(i))))
            return np.array(closest), self.df.loc[np.array(sorted(closest, key=lambda x: x[1]))[:,0]]

        except:     
            closest=(([(0,0)]))
            
            return np.array(closest), self.df.loc[np.array(sorted(closest, key=lambda x: x[1]))[:,0]]

        
        
        
#         for i in km_cluster:
#             if i != title_idx:
#                 closest.append((i,euclidean(data_svd_dict.get(title_idx), data_svd_dict.get(i))))

#         return np.array(closest), self.df.loc[np.array(sorted(closest, key=lambda x: x[1]))[:,0]]

    def result_by_weights(self, dataf):
        dataf['weighted_sum'] = dataf['dist_scaled']*self.a + dataf['genre_scaled']*self.b + dataf['wvote_scaled']*self.c
        
        return dataf.sort_values('weighted_sum', ascending=False)

            
    def getMovies(self, title):
        # no title result
        try: title_idx = self.df[self.df['title']== title].index.values[0]
        except:
            raise ValueError('There is no such title name. Search with "search_title" function')
        
        # get movies in same cluster
        dist, result = self.similar_cluster_movies(title_idx)
        
        # merge with distance
        result = pd.merge(result, pd.Series(dist[:,1], name='dist'), left_on=result.index, right_on=dist[:,0])
        result.rename(columns={'key_0':'idx'}, inplace=True)
        
        # IMDB's weighted_vote
        def weighted_vote_average(record):
            v, r = record['vote_count'], record['rating']
            return (v/(v+m))*r + (m/(m+v))*c
        c = result['rating'].mean()
        m = result['vote_count'].quantile(.6)
        result['weighted_vote'] = result.apply(weighted_vote_average,axis=1)
        
        # merge with genre
        genre_sim = self.genre_sim_sorted(title_idx)
        result_with_genre = pd.merge(result, pd.Series(genre_sim[:,1], name='genre_sim'), left_on=result.idx, right_on=genre_sim[:,0],)
        
        # minmax scale
        result_with_genre['wvote_scaled'] = MinMaxScaler().fit_transform(result_with_genre['weighted_vote'].values.reshape(-1,1))
        result_with_genre['genre_scaled'] = MinMaxScaler().fit_transform(result_with_genre['genre_sim'].values.reshape(-1,1))
        result_with_genre['dist_scaled'] = MinMaxScaler().fit_transform(result_with_genre['dist'].max() - result_with_genre['dist'].values.reshape(-1,1))
        
        # (optional)remove data with 0 genre score
        no_genre_score_idx = result_with_genre[result_with_genre['genre_sim'] == 0].index
        result_with_genre.drop(no_genre_score_idx, inplace=True)
        
        result_with_genre = self.result_by_weights(result_with_genre)
        return result_with_genre.head(self.topn)

In [30]:
def get_ctt(goal,model):
    if model == 'tf':
        idx = id2title[goal]
        goalcate=goal[0]
        same_sim_scores=[]
        diff_sim_scores=[]
        for i,c in enumerate(cosine_matrix[idx]):
            if title2id[i][0] ==goalcate and i !=idx:
                same_sim_scores.append((i,c))
            if title2id[i][0]!=goalcate:
                diff_sim_scores.append((i,c))
        same_sim_scores = sorted(same_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        diff_sim_scores = sorted(diff_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        same_result = [(title2id[i], score) for i, score in same_sim_scores]
        diff_result=[(title2id[i], score) for i, score in diff_sim_scores]
        same_result=pd.DataFrame(same_result)
        diff_result=pd.DataFrame(diff_result)
        same_result.columns=['title','similarity']
        diff_result.columns=['title','similarity']
        result=pd.concat([same_result,diff_result],axis=1)
        
        return diff_result
        
    elif model == 'clust':
        goals = df[df['title']==goal]
        if goal[0]=='m':
            nowdf = bookdf.append(goals)
        elif goal[0]=='b':
            nowdf = moviedf.append(goals)
        fname = './data/now_for_cluster.csv'
        nowdf.to_csv(fname)
        try:
            recom = cross_recommendation_cluster(re_cluster=True)
            result = recom.getMovies(goal)
            diff_result = result[['title','weighted_sum']]
            diff_result.columns=['title','similarity']
            return diff_result
        except:
            pass


In [31]:
def get_ctt_b(goal,model):
    if model == 'tf':
        idx = id2title[goal]
        goalcate=goal[0]
        same_sim_scores=[]
        diff_sim_scores=[]
        for i,c in enumerate(cosine_matrix[idx]):
            if title2id[i][0] ==goalcate and i !=idx:
                same_sim_scores.append((i,c))
            if title2id[i][0]!=goalcate:
                diff_sim_scores.append((i,c))
        same_sim_scores = sorted(same_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        diff_sim_scores = sorted(diff_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        same_result = [(title2id[i], score) for i, score in same_sim_scores]
        diff_result=[(title2id[i], score) for i, score in diff_sim_scores]
        same_result=pd.DataFrame(same_result)
        diff_result=pd.DataFrame(diff_result)
        same_result.columns=['title','similarity']
        diff_result.columns=['title','similarity']
        result=pd.concat([same_result,diff_result],axis=1)
        return same_result
    
    
    elif model == 'clust':

        try:
            recom = book_recommendation_cluster(re_cluster=True)
            result = recom.getMovies(goal)
            same_result = result[['title','weighted_sum']]
            same_result.columns=['title','similarity']
            return same_result
        except:
            pass

    



In [32]:
def get_ans(user,book):
    ans=newdf[['title',user]]
    try:
        res=ans[ans['title']==book].values[0][1]
    except:
        res=0
    return res

In [33]:
newdf.head(3)

Unnamed: 0              userid 24BqEWE785rjn  2mwvg7EagvMa7  2mwvgaAjwxMa7  \
1           1  b10 1/2장으로 쓴 세계 역사           NaN            NaN            NaN   
2           2         b1001개의 거짓말           NaN            NaN            NaN   
3           3                b11분           NaN            3.0            3.5   

   2mwvgbGLgqMa7  2mwvggAE2vMa7  2mwvgLpo25Ma7  2mwvgYmarxMa7  36lvX3jzZqXdn  \
1            NaN            NaN            NaN            NaN            NaN   
2            NaN            NaN            NaN            NaN            NaN   
3            NaN            NaN            3.5            4.5            NaN   

   ...  ZBm5RVn735d46  zNM5N1gz7v26j  zNM5NARwPGv26  ZWpqMaWa1qrkn  \
1  ...            NaN            NaN            NaN            NaN   
2  ...            NaN            NaN            NaN            NaN   
3  ...            NaN            NaN            NaN            NaN   

   ZWpqMMERlqrkn   총합계               title  rating  vote_count  content  
1            NaN   4.0  b10 1/2장으로 쓴 세계 역사     4.0         1.0        b  
2            NaN   3.5         b1001개의 거짓말     3.5         1.0        b  
3            NaN  77.0                b11분     3.5        22.0        b  

[3 rows x 118 columns]

In [34]:
newdf[newdf['title']=='b아몬드'].values[0][1]

'b아몬드'

In [35]:
def get_vtcnt(book):
    ans=newdf[['title','vote_count']]
    try:
        res=ans[ans['title']==book].values[0][1]
    except:
        res=0
    return res

In [36]:
def get_avg_rt(book):
    ans=newdf[['title','rating']]
    try:
        res=ans[ans['title']==book].values[0][1]
    except:
        res=0
    return res

In [37]:
search = goal

## Eval

In [38]:
atitle2id = {}
for i, c in enumerate(newdf['title']): atitle2id[i] = c

# id와 movie title를 매핑할 dictionary를 생성해줍니다. 
aid2title = {}
for i, c in atitle2id.items(): aid2title[c] = i

In [39]:
def user_pref(user,model):
    a=newdf[newdf[user]>=4.5].sort_values(by='rating', ascending=False).head(30)
    a=a[['title','rating','vote_count','content']]
    # m = 사용자가 평점 높게 준 영화 목록
    m = a[a['content']=='m'].head(20)
    m=m['title'].values
    #각 영화와 유사도 높은 책 목록 구하기
    rec_book=dict()
    for movie in m:
#         for i in range(10):
#             book, sim = get_ctt(movie).iloc[0][0] , get_ctt(movie).iloc[0][1]
#         for book in get_ctt(movie)['title'][:3]:
        print(movie)  
        for book in get_ctt(movie,model)['title']:
#             print(book)
            if book not in rec_book:
                rec_book[book]=1
            elif book in rec_book:
                rec_book[book]+=1
    rec_book=pd.DataFrame.from_dict(rec_book,orient='index')
    rec_book.columns=['sim']
    ## 책 목록에 대하여 유저가 남긴 평점 구하기
    return rec_book
    
    

In [40]:
## 책함수채우기
def book_fc(data):
    rats=[]
    vc=[]
    avg_rt=[]
    for i in range(len(data)):
        book = data.index[i]
        rat = get_ans(user,book)
        vote= get_vtcnt(book)
        avg_rating=get_avg_rt(book)
        rats.append(rat)
        vc.append(vote)
        avg_rt.append(avg_rating)
    data['user_rating']=rats
    data['vote_count']=vc
    data['avg_rating']=avg_rt
    return data

In [41]:
def rmse(y,pred):
    mse = mean_squared_error(y,pred)
    return np.sqrt(mse)
def mae(y,pred):
    return mean_absolute_error(y,pred)
def mape(y,pred):
    return np.mean(np.abs((y-pred)/y)*100)

In [42]:
def user_pref_book(user,min_rt):
    a=newdf[newdf[user]>=min_rt].sort_values(by='rating', ascending=False)
    a=a[['title','rating','vote_count','content']]
    # m = 사용자가 평점 높게 준 영화 목록
    m = a[a['content']=='b']
    m=m['title'].values
    return m
    
    

# cross_recommendation_cluster

In [47]:
models=['tf','clust']

In [48]:
user=input('user를 입력하세요')


user를 입력하세요ZWpqMaWa1qrkn


In [49]:
model = input('model을 입력하세요')

model을 입력하세요tf


In [50]:
user

'ZWpqMaWa1qrkn'

In [51]:
model

'tf'

In [52]:
rec_book=user_pref(user,model)

m인셉션
m이터널 선샤인
m위플래쉬
m기생충
m스포트라이트
m센과 치히로의 행방불명
m블랙 스완
m디 아워스
m타오르는 여인의 초상
m인사이드 아웃
m올드보이
m셰이프 오브 워터: 사랑의 모양
m퍼펙트 블루
m하나 그리고 둘
m케빈에 대하여
m2001 스페이스 오디세이
m더 페이버릿: 여왕의 여자
m델마와 루이스
m나를 찾아줘
m조조 래빗


In [53]:
rats=[]
vc=[]
avg_rt=[]
for i in range(len(rec_book)):
    book = rec_book.index[i]
    rat = get_ans(user,book)
    vote= get_vtcnt(book)
    avg_rating=get_avg_rt(book)
    rats.append(rat)
    vc.append(vote)
    avg_rt.append(avg_rating)
rec_book['user_rating']=rats
rec_book['vote_count']=vc
rec_book['avg_rating']=avg_rt

rec_book=rec_book.fillna(0)
rec_book

sim  user_rating  vote_count  avg_rating
b영화를 찍으며 생각한 것    1          0.0        10.0         3.9
b바보 만들기           1          0.0         1.0         3.0
b뒷모습              1          0.0         3.0         3.3
b아몬드              5          0.0        30.0         3.3
b채식주의자            2          0.0        53.0         3.7
...             ...          ...         ...         ...
b나의 라임 오렌지나무      1          0.0        45.0         4.1
b데미안              1          0.0        61.0         4.1
b고도를 기다리며         1          0.0        20.0         3.8
b잘못은 우리 별에 있어     1          0.0         9.0         3.4
b양철북              1          0.0         3.0         4.2

[225 rows x 4 columns]

## 평점 계산

In [54]:
user_3 = user_pref_book(user,3)
recall_m=len(user_3)
recall_m

18

In [58]:
def weight(record, m=m, C=C):
    v= record['vote_count']
    R=record['avg_rating']
    S=record['sim']
    return ((v/(v+m))*R)+((m/(m+v))*C+(v/v+m)*0.02)


In [59]:
percentile=0.9
m=rec_book['vote_count'].quantile(percentile)
C=rec_book['avg_rating'].mean()
rec_book['pred']=rec_book.apply(weight,axis=1)
rec_book=rec_book.fillna(0)
#사용자 평점 있는 책
user_rec=rec_book[rec_book['user_rating']>0]
min_rec=min(user_rec['user_rating'].values)
y=user_rec['user_rating']
pred=user_rec['pred']
#user가 3점 이상 준 모든 책
user_3 = user_pref_book(user,3)

y=user_rec['user_rating']
pred=user_rec['pred']
user_like=len(rec_book[rec_book['user_rating']>3.5])
recal=user_like/recall_m
prek=user_like/len(user_rec)


len(user_rec)

7

In [60]:
print('user가 3점 이상 준 모든 책 : ',len(user_3))
print('내가 추천한 것 중 user 평점 있는 책 :',len(user_rec))
print('내가 추천한 것 중 user가 3점 이상 준 책 : ', user_like)

user가 3점 이상 준 모든 책 :  18
내가 추천한 것 중 user 평점 있는 책 : 7
내가 추천한 것 중 user가 3점 이상 준 책 :  4


In [61]:
rec_book.sort_values(by=['pred'],ascending=False)

sim  user_rating  vote_count  avg_rating      pred
b1984           1          0.0        47.0         4.3  4.530471
b동물농장           1          0.0        49.0         4.2  4.463399
b데미안            1          0.0        61.0         4.1  4.407639
b입 속의 검은 잎      1          0.0        19.0         4.3  4.405556
b나의 라임 오렌지나무    1          0.0        45.0         4.1  4.384549
...           ...          ...         ...         ...       ...
b아몬드            5          0.0        30.0         3.3  3.859410
b페인트            2          0.0         5.0         2.4  3.837963
b우리들의 행복한 시간    1          0.0        26.0         3.2  3.815802
b돌이킬 수 없는 약속    2          0.0         9.0         2.7  3.786111
b지도 밖으로 행군하라    1          0.0        25.0         2.8  3.593434

[225 rows x 5 columns]

In [62]:
y=user_rec['user_rating']
pred=user_rec['pred']
user_like=len(rec_book[rec_book['user_rating']>3.5])
recal=user_like/recall_m
prek=user_like/len(user_rec)

evaldict[user+' '+model+' '+'cross'+' '+'RMSE']=rmse(y,pred)

evaldict[user+' '+model+' '+'cross'+' ''MAE']=mae(y,pred)

evaldict[user+' '+model+' '+'cross'+' ''MAPE ']=mape(y,pred)

evaldict[user+' '+model+' '+'cross'+' ''Recall@K'] = recal

evaldict[user+' '+model+' '+'cross'+' ''Precision@K']=prek


print('RMSE : ', rmse(y,pred))
print('MAE : ', mae(y,pred))
print('MAPE : ', mape(y,pred))
print('Recall@K : ', recal)
print('Precision@K : ',prek)

RMSE :  0.7369446341828925
MAE :  0.5865941738526281
MAPE :  17.064233173175307
Recall@K :  0.2222222222222222
Precision@K :  0.5714285714285714


In [63]:
evaldict

{'ZWpqMaWa1qrkn tf cross RMSE': 0.7369446341828925,
 'ZWpqMaWa1qrkn tf cross MAE': 0.5865941738526281,
 'ZWpqMaWa1qrkn tf cross MAPE ': 17.064233173175307,
 'ZWpqMaWa1qrkn tf cross Recall@K': 0.2222222222222222,
 'ZWpqMaWa1qrkn tf cross Precision@K': 0.5714285714285714}

## 책기반 책추천시스템


In [64]:
len(rec_book)>0

True

In [65]:
def user_pref_b(user,model):
    a=newdf[newdf[user]>=3].sort_values(by='rating', ascending=False)
    a=a[['title','rating','vote_count','content']]
    # m = 사용자가 평점 높게 준 책 목록
    m = a[a['content']=='b']
    m=m['title'].values
    #각 책 유사도 높은 책 목록 구하기
    rec_book=dict()
    for movie in m:
#         print(movie)
        try:
            for book in get_ctt_b(movie,model)['title']:
                if book not in rec_book:
                    rec_book[book]=1
                elif book in rec_book:
                    rec_book[book]+=1
        except:
            rec_book = before
    rec_book=pd.DataFrame.from_dict(rec_book,orient='index')
    rec_book.columns=['sim']
    before=rec_book
    ## 책 목록에 대하여 유저가 남긴 평점 구하기
    return rec_book
    

In [66]:
bbyb= user_pref_b(user,model)

In [67]:

bbyb=book_fc(bbyb)
bbyb=bbyb.fillna(0)

In [68]:
bbyb

sim  user_rating  vote_count  avg_rating
b68년의 나날들, 조선의 일상사    1          0.0         1.0         4.5
b그 남자네 집              2          0.0         7.0         4.1
b노인을 위한 나라는 없다        3          4.0         5.0         4.0
bGO                   2          0.0        12.0         3.6
b타오르는 마음              2          0.0         1.0         4.0
...                 ...          ...         ...         ...
b달의 궁전                1          0.0        11.0         3.9
b테스                   1          0.0        11.0         3.5
b달콤 쌉싸름한 초콜릿          1          0.0         9.0         3.8
b등대로                  1          0.0         1.0         4.5
b인간 실격                1          0.0        55.0         4.0

[205 rows x 4 columns]

In [69]:
percentile=0.6
m=bbyb['vote_count'].quantile(percentile)
C=bbyb['avg_rating'].mean()
bbyb['pred']=bbyb.apply(weight,axis=1)
user_rec_b=bbyb[bbyb['user_rating']>0]
y=user_rec_b['user_rating']
pred=user_rec_b['pred']
user_like=len(user_rec_b)
recal=user_like/recall_m
prek=user_like/len(bbyb)


In [70]:
user_rec_b

sim  user_rating  vote_count  avg_rating      pred
b노인을 위한 나라는 없다    3          4.0         5.0         4.0  4.171296
b콜 미 바이 유어 네임     4          2.5        12.0         3.8  4.145520
b완득이              1          3.5        37.0         3.5  3.971627
b죽은 시인의 사회        1          4.0        15.0         3.7  4.106209
b슬럼독 밀리어네어        1          4.0         7.0         4.0  4.188889
b플립               1          4.0         2.0         4.5  4.186243
b흐르는 강물처럼         1          4.0         3.0         3.7  4.109596
b심판               2          4.5         4.0         3.5  4.074396
b로미오와 줄리엣         1          3.5        18.0         3.8  4.154354
b자전거 도둑           1          4.0         8.0         3.5  4.048560

In [71]:
print('user가 3점 이상 준 모든 책 : ',len(user_3))
print('내가 추천한 것 중 user 평점 있는 책 :',len(user_rec_b))
print('내가 추천한 것 중 user가 3점 이상 준 책 : ', user_like)

user가 3점 이상 준 모든 책 :  18
내가 추천한 것 중 user 평점 있는 책 : 10
내가 추천한 것 중 user가 3점 이상 준 책 :  10


In [72]:


evaldict[user+' '+model+' '+'book'+' '+'RMSE']=rmse(y,pred)

evaldict[user+' '+model+' '+'book'+' '+'MAE']=mae(y,pred)

evaldict[user+' '+model+' '+'book'+' '+'MAPE ']=mape(y,pred)

evaldict[user+' '+model+' '+'book'+' '+'Recall@K'] = recal

evaldict[user+' '+model+' '+'book'+' '+'Precision@K']=prek




print('RMSE : ', rmse(y,pred))
print('MAE : ', mae(y,pred))
print('MAPE : ', mape(y,pred))
print('Recall@K : ', recal)
print('Precision@K : ',prek)

RMSE :  0.6053794794687004
MAE :  0.4007898268610511
MAPE :  12.771938137973986
Recall@K :  0.5555555555555556
Precision@K :  0.04878048780487805


In [73]:
evaldict

{'ZWpqMaWa1qrkn tf cross RMSE': 0.7369446341828925,
 'ZWpqMaWa1qrkn tf cross MAE': 0.5865941738526281,
 'ZWpqMaWa1qrkn tf cross MAPE ': 17.064233173175307,
 'ZWpqMaWa1qrkn tf cross Recall@K': 0.2222222222222222,
 'ZWpqMaWa1qrkn tf cross Precision@K': 0.5714285714285714,
 'ZWpqMaWa1qrkn tf book RMSE': 0.6053794794687004,
 'ZWpqMaWa1qrkn tf book MAE': 0.4007898268610511,
 'ZWpqMaWa1qrkn tf book MAPE ': 12.771938137973986,
 'ZWpqMaWa1qrkn tf book Recall@K': 0.5555555555555556,
 'ZWpqMaWa1qrkn tf book Precision@K': 0.04878048780487805}

## eval dict

In [92]:
evaldict

{'ZWpqMaWa1qrkn tf cross RMSE': 0.7369446341828925,
 'ZWpqMaWa1qrkn tf cross MAE': 0.5865941738526281,
 'ZWpqMaWa1qrkn tf cross MAPE ': 17.064233173175307,
 'ZWpqMaWa1qrkn tf cross Recall@K': 0.2222222222222222,
 'ZWpqMaWa1qrkn tf cross Precision@K': 0.5714285714285714,
 'ZWpqMaWa1qrkn tf book RMSE': 0.6053794794687004,
 'ZWpqMaWa1qrkn tf book MAE': 0.4007898268610511,
 'ZWpqMaWa1qrkn tf book MAPE ': 12.771938137973986,
 'ZWpqMaWa1qrkn tf book Recall@K': 0.5555555555555556,
 'ZWpqMaWa1qrkn tf book Precision@K': 0.04878048780487805,
 '2mwvg7EagvMa7 tf cross RMSE': 1.105398925814795,
 '2mwvg7EagvMa7 tf cross MAE': 1.0040998013194828,
 '2mwvg7EagvMa7 tf cross MAPE ': 34.810110392990005,
 '2mwvg7EagvMa7 tf cross Recall@K': 0.09259259259259259,
 '2mwvg7EagvMa7 tf cross Precision@K': 0.2,
 '2mwvg7EagvMa7 tf book RMSE': 0.9968007592696619,
 '2mwvg7EagvMa7 tf book MAE': 0.9019144855016129,
 '2mwvg7EagvMa7 tf book MAPE ': 29.781183712933757,
 '2mwvg7EagvMa7 tf book Recall@K': 0.7962962962962963

In [116]:
a=list(evaldict.items())

In [117]:
a[0][1]

0.7369446341828925

In [118]:
eval_df=pd.DataFrame(columns=['user','model','domain','evaluation','result'])

In [119]:
u=[]
m=[]
d=[]
e=[]
r=[]
for bb in a:
    now = bb[0].split(' ')
    if now[0] not in u:
        u.append(now[0])
    else:
        u.append(' ')
    m.append(now[1])
    d.append(now[2])
    e.append(now[3])
    r.append(bb[1])

In [99]:
q=eval_df

In [102]:
q

model domain   evaluation     result
user                                              
2mwvg7EagvMa7    tf  cross         RMSE   1.105399
                 tf  cross          MAE   1.004100
                 tf  cross         MAPE  34.810110
                 tf  cross     Recall@K   0.092593
                 tf  cross  Precision@K   0.200000
...             ...    ...          ...        ...
                 tf   book         RMSE   0.985605
                 tf   book          MAE   0.795156
                 tf   book         MAPE  28.389781
                 tf   book     Recall@K   0.720000
                 tf   book  Precision@K   0.096000

[340 rows x 4 columns]

In [121]:
len(eval_df)

895

In [122]:
895//10

89

In [123]:
eval_df.head()

model domain   evaluation     result
user                                              
ZWpqMaWa1qrkn    tf  cross         RMSE   0.736945
                 tf  cross          MAE   0.586594
                 tf  cross         MAPE  17.064233
                 tf  cross     Recall@K   0.222222
                 tf  cross  Precision@K   0.571429

In [124]:
q.head()

model domain   evaluation     result
user                                              
2mwvg7EagvMa7    tf  cross         RMSE   1.105399
                 tf  cross          MAE   1.004100
                 tf  cross         MAPE  34.810110
                 tf  cross     Recall@K   0.092593
                 tf  cross  Precision@K   0.200000

In [115]:
len(q.index)

340

In [100]:
len(q)

340

In [125]:
q=q.append(eval_df)

In [126]:
len(q)

1235

In [120]:
eval_df.user=u
eval_df.model=m
eval_df.domain=d
eval_df.evaluation=e
eval_df.result=r
eval_df=eval_df.set_index('user')

In [130]:
us = q.index.drop_duplicates()

In [127]:
q.to_csv('./data/eval_tf.csv')

In [131]:
len(us)

91

In [109]:
us

Index(['2mwvg7EagvMa7', ' ', '2mwvgaAjwxMa7', '2mwvgbGLgqMa7', '2mwvggAE2vMa7',
       '2mwvgLpo25Ma7', '2mwvgYmarxMa7', '36lvX3jzZqXdn', '36lvXmWQZ5Xdn',
       '3BnvwpKaj5PAY', '3BnvwZ6bZqPAY', '4WLxZaDz65roA', '4WLxZaXN75roA',
       '4WLxZB8nkxroA', '4WLxZKgdmqroA', '4WLxZmblW5roA', '4WLxZZ3wkxroA',
       '4WLxZZ7D8xroA', '6ADvG0XPK5zZl', '6ADvGZ98eqzZl', '6ewxaPbAwO5Q1',
       '6NW5Qb02wx1Yo', '6NW5QB9Lyx1Yo', '6NW5QBDzwx1Yo', '6NW5QzzJkx1Yo',
       '7gdxdr7e9vGYJ', '87Gv741ND5E6o', '87Gv7bQzmqE6o', '8BRve6JpL56VJ',
       '8nPvyGzRZxYo0', '박지수', '영화고독발버둥치며본다', '진',
       'a9L5PGKL2vwg8', 'a9L5PJm1Bqwg8'],
      dtype='object', name='user')

In [ ]:
users[35:]

only contents

In [88]:
def get_ctt_only_content(goal,model):
    if model == 'tf':
        idx = id2title[goal]
        goalcate=goal[0]
        same_sim_scores=[]
        diff_sim_scores=[]
        for i,c in enumerate(cosine_matrix[idx]):
            if title2id[i][0] ==goalcate and i !=idx:
                same_sim_scores.append((i,c))
            if title2id[i][0]!=goalcate:
                diff_sim_scores.append((i,c))
        same_sim_scores = sorted(same_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        diff_sim_scores = sorted(diff_sim_scores, key = lambda x: x[1], reverse=True)[0:15]
        same_result = [(title2id[i], score) for i, score in same_sim_scores]
        diff_result=[(title2id[i], score) for i, score in diff_sim_scores]
        same_result=pd.DataFrame(same_result)
        diff_result=pd.DataFrame(diff_result)
        same_result.columns=['title','similarity']
        diff_result.columns=['title','similarity']
        result=pd.concat([same_result,diff_result],axis=1)
        diff_result= diff_result[:1]
        
        return diff_result
        
    elif model == 'clust':
        goals = df[df['title']==goal]
        if goal[0]=='m':
            nowdf = bookdf.append(goals)
        elif goal[0]=='b':
            nowdf = moviedf.append(goals)
        fname = './data/now_for_cluster.csv'
        nowdf.to_csv(fname)
        try:
            recom = cross_recommendation_cluster(re_cluster=True)
            result = recom.getMovies(goal)
            diff_result = result[['title','weighted_sum']]
            diff_result.columns=['title','similarity']
            return diff_result
        except:
            pass


In [92]:
#사용자 기록 배제 추천시스템
def user_pref_ctt(user,model):
    a=newdf[newdf[user]>=4.5].sort_values(by='rating', ascending=False).head(30)
    a=a[['title','rating','vote_count','content']]
    # m = 사용자가 평점 높게 준 영화 목록
    m = a[a['content']=='m'].head(20)
    m=m['title'].values
    #각 영화와 유사도 높은 책 목록 구하기
    rec_book=dict()
    for movie in m:
#         for i in range(10):
#             book, sim = get_ctt(movie).iloc[0][0] , get_ctt(movie).iloc[0][1]
#         for book in get_ctt(movie)['title'][:3]:
        print(movie)  
        for book in get_ctt_only_content(movie,model)['title']:
#             print(book)
            if book not in rec_book:
                rec_book[book]=1
            elif book in rec_book:
                rec_book[book]+=1
    rec_book=pd.DataFrame.from_dict(rec_book,orient='index')
    rec_book.columns=['sim']
    ## 책 목록에 대하여 유저가 남긴 평점 구하기
    return rec_book
    

m인셉션
m이터널 선샤인
m위플래쉬
m기생충
m스포트라이트
m센과 치히로의 행방불명
m블랙 스완
m디 아워스
m타오르는 여인의 초상
m인사이드 아웃
m올드보이
m셰이프 오브 워터: 사랑의 모양
m퍼펙트 블루
m하나 그리고 둘
m케빈에 대하여
m2001 스페이스 오디세이
m더 페이버릿: 여왕의 여자
m델마와 루이스
m나를 찾아줘
m조조 래빗


m인셉션
m이터널 선샤인
m위플래쉬
m기생충
m스포트라이트
m센과 치히로의 행방불명
m블랙 스완
m디 아워스
m타오르는 여인의 초상
m인사이드 아웃
m올드보이
m셰이프 오브 워터: 사랑의 모양
m퍼펙트 블루
m하나 그리고 둘
m케빈에 대하여
m2001 스페이스 오디세이
m더 페이버릿: 여왕의 여자
m델마와 루이스
m나를 찾아줘
m조조 래빗


In [104]:
evaldict

{'ZWpqMaWa1qrkn tf onlyctt RMSE': 0,
 'ZWpqMaWa1qrkn tf onlyctt MAE': 0,
 'ZWpqMaWa1qrkn tf onlyctt MAPE ': 0,
 'ZWpqMaWa1qrkn tf onlyctt Recall@K': 0,
 'ZWpqMaWa1qrkn tf onlyctt Precision@K': 0}

In [95]:
rec_book

sim  user_rating  vote_count  avg_rating      pred
b영화를 찍으며 생각한 것     1          0.0        10.0         3.9  4.176245
b별들의 들판            1          0.0         1.0         3.0  4.075556
b앨저넌에게 꽃을          1          0.0         2.0         4.0  4.138624
b나쁜 피              1          0.0         1.0         3.5  4.100556
b기억 전달자            1          0.0        10.0         4.0  4.210728
b달콤 쌉싸름한 초콜릿       1          0.0         9.0         3.8  4.139683
b예브게니 오네긴          2          0.0         3.0         4.0  4.150505
b등대로               1          0.0         1.0         4.5  4.150556
b돌이킬 수 없는 약속       1          0.0         9.0         2.7  3.786111
b라프 코스터의 재미이론      1          0.0         1.0         4.0  4.125556
b2001 스페이스 오디세이    1          0.0         2.0         4.3  4.167196
b불한당들의 세계사         1          0.0         3.0         3.7  4.109596
b아몬드               1          0.0        30.0         3.3  3.859410
b달콤한 나의 도시         1          0.0        10.0         3.2  3.934866
b파우스트              1          0.0        19.0         4.2  4.355556
b햄릿                1          0.0        24.0         4.1  4.328165
b용의자 X의 헌신         1          0.0        34.0         3.8  4.168134
b노란 손수건            1          0.0         2.0         3.8  4.119577
b안네의 일기            1          0.0        28.0         4.1  4.342790

## 전체 코드

In [84]:
for model in models:
    print(model)

tf


In [83]:
models=['tf']

In [86]:
users

Index(['24BqEWE785rjn', '2mwvg7EagvMa7', '2mwvgaAjwxMa7', '2mwvgbGLgqMa7',
       '2mwvggAE2vMa7', '2mwvgLpo25Ma7', '2mwvgYmarxMa7', '36lvX3jzZqXdn',
       '36lvXmWQZ5Xdn', '3BnvwpKaj5PAY',
       ...
       'YMKqmLrErxloD', 'YMKqmne6Pkvlo', 'YMKqmwrVr5loD', 'ZBm5Rgkl9xd46',
       'ZBm5RNnk95d46', 'ZBm5RVn735d46', 'zNM5N1gz7v26j', 'zNM5NARwPGv26',
       'ZWpqMaWa1qrkn', 'ZWpqMMERlqrkn'],
      dtype='object', length=111)

In [88]:
newdf[newdf['24BqEWE785rjn']]

SyntaxError: EOL while scanning string literal (3213379133.py, line 1)

In [114]:
for user in users[37:]:
    for model in models:
        rec_book=user_pref(user,model)
        rats=[]
        vc=[]
        avg_rt=[]
        for i in range(len(rec_book)):
            book = rec_book.index[i]
            rat = get_ans(user,book)
            vote= get_vtcnt(book)
            avg_rating=get_avg_rt(book)
            rats.append(rat)
            vc.append(vote)
            avg_rt.append(avg_rating)
        rec_book['user_rating']=rats
        rec_book['vote_count']=vc
        rec_book['avg_rating']=avg_rt

        rec_book=rec_book.fillna(0)
        user_3 = user_pref_book(user,3)
        recall_m=len(user_3)
        percentile=0.9
        m=rec_book['vote_count'].quantile(percentile)
        C=rec_book['avg_rating'].mean()
        rec_book['pred']=rec_book.apply(weight,axis=1)
        rec_book=rec_book.fillna(0)
        #사용자 평점 있는 책
        user_rec=rec_book[rec_book['user_rating']>0]
        min_rec=min(user_rec['user_rating'].values)
        y=user_rec['user_rating']
        pred=user_rec['pred']
        #user가 3점 이상 준 모든 책
        user_3 = user_pref_book(user,3)

        y=user_rec['user_rating']
        pred=user_rec['pred']
        user_like=len(rec_book[rec_book['user_rating']>3.5])
        recal=user_like/recall_m
        prek=user_like/len(user_rec)
        y=user_rec['user_rating']
        pred=user_rec['pred']
        user_like=len(rec_book[rec_book['user_rating']>3.5])
        recal=user_like/recall_m
        prek=user_like/len(user_rec)

        evaldict[user+' '+model+' '+'cross'+' '+'RMSE']=rmse(y,pred)

        evaldict[user+' '+model+' '+'cross'+' ''MAE']=mae(y,pred)

        evaldict[user+' '+model+' '+'cross'+' ''MAPE ']=mape(y,pred)

        evaldict[user+' '+model+' '+'cross'+' ''Recall@K'] = recal

        evaldict[user+' '+model+' '+'cross'+' ''Precision@K']=prek
        
        
        ####책
        bbyb= user_pref_b(user,model)
        bbyb=book_fc(bbyb)
        bbyb=bbyb.fillna(0)
        
        
        percentile=0.6
        m=bbyb['vote_count'].quantile(percentile)
        C=bbyb['avg_rating'].mean()
        bbyb['pred']=bbyb.apply(weight,axis=1)
        user_rec_b=bbyb[bbyb['user_rating']>0]
        y=user_rec_b['user_rating']
        pred=user_rec_b['pred']
        user_like=len(user_rec_b)
        recal=user_like/recall_m
        prek=user_like/len(bbyb)
        

        evaldict[user+' '+model+' '+'book'+' '+'RMSE']=rmse(y,pred)

        evaldict[user+' '+model+' '+'book'+' '+'MAE']=mae(y,pred)

        evaldict[user+' '+model+' '+'book'+' '+'MAPE ']=mape(y,pred)

        evaldict[user+' '+model+' '+'book'+' '+'Recall@K'] = recal

        evaldict[user+' '+model+' '+'book'+' '+'Precision@K']=prek


m자연의 아이들
m란
m스위티
m어느 가족
m그린 나이트
m기생충
m로마
m피닉스
m라라랜드
m퍼스트 카우
m블레이드 러너
m셰이프 오브 워터: 사랑의 모양
m소울
m큐어
m타오르는 여인의 초상
m드라이브 마이 카
m토니 에드만
m밀리언 달러 베이비
m더 파더
m자마
m피나
m걸어도 걸어도
m라라랜드
m센과 치히로의 행방불명
m보이후드
m파이트 클럽
m월-E
m심플 라이프
m동주
m천국보다 낯선
m굿 윌 헌팅
m조제, 호랑이 그리고 물고기들
m밤의 해변에서 혼자
m사랑의 블랙홀
m봄날은 간다
m하트비트
m레인 오버 미
m400번의 구타
m노킹 온 헤븐스 도어
m박쥐
m검은 고양이 흰 고양이
m리벨리온
m어웨이 프롬 허
m나에게서 온 편지
m씨민과 나데르의 별거
m나라야마 부시코
m걸어도 걸어도
m시
m쇼생크 탈출
m하얀 리본
m순응자
m위플래쉬
m인생은 아름다워
m어느 가족
m라스베가스를 떠나며
m살인의 추억
m귀신이 온다
m로마
m칼리토
m인셉션
m쇼생크 탈출
m위플래쉬
m라라랜드
m타이타닉
m어바웃 타임
m스포트라이트
m다크 나이트
m레옹
m죽은 시인의 사회
m다크 나이트 라이즈
m덩케르크
m굿 윌 헌팅
m피아니스트
m하울의 움직이는 성
m식스 센스
m토이 스토리
m오페라의 유령 : 25주년 특별 공연
m라이온 킹
m글래디에이터
m베카신!
m가나의 혼인잔치: 언약
m12번째 솔저
m보이콰이어
m베를린 호스티지
m리틀 큐
m레미: 집 없는 아이
m집 이야기
m에이브의 쿠킹 다이어리
m마이 스파이
m내겐 너무 소중한 너
m왼팔의복서 닉
m치어리딩 클럽
m벌룬
m타임 체인저
m한창나이 선녀님
m들리나요?
m사랑이 지나간 자리
m아홉수 로맨스
m메이드 인 이태리
m어바웃 타임
m토이 스토리 3
m토이 스토리
m일주일간 친구
m항거:유관순 이야기
m시간을 달리는 소녀
m오렌지
m님아, 그 강을 건너지 마오
m알라딘
m겨울왕국
m당신이 잠든 사이에
m리틀 포레스트: 여름과 가을
m미쓰백
m겨울왕국 2
m굿모닝 에브리원
m정직한 후보
m걸캅스
m인셉션
m쇼생크 탈출
m

UnboundLocalError: local variable 'before' referenced before assignment

In [90]:
evaldict

{'ZWpqMaWa1qrkn tf cross RMSE': 0.7369446341828925,
 'ZWpqMaWa1qrkn tf cross MAE': 0.5865941738526281,
 'ZWpqMaWa1qrkn tf cross MAPE ': 17.064233173175307,
 'ZWpqMaWa1qrkn tf cross Recall@K': 0.2222222222222222,
 'ZWpqMaWa1qrkn tf cross Precision@K': 0.5714285714285714,
 'ZWpqMaWa1qrkn tf book RMSE': 0.6053794794687004,
 'ZWpqMaWa1qrkn tf book MAE': 0.4007898268610511,
 'ZWpqMaWa1qrkn tf book MAPE ': 12.771938137973986,
 'ZWpqMaWa1qrkn tf book Recall@K': 0.5555555555555556,
 'ZWpqMaWa1qrkn tf book Precision@K': 0.04878048780487805,
 '2mwvg7EagvMa7 tf cross RMSE': 1.105398925814795,
 '2mwvg7EagvMa7 tf cross MAE': 1.0040998013194828,
 '2mwvg7EagvMa7 tf cross MAPE ': 34.810110392990005,
 '2mwvg7EagvMa7 tf cross Recall@K': 0.09259259259259259,
 '2mwvg7EagvMa7 tf cross Precision@K': 0.2,
 '2mwvg7EagvMa7 tf book RMSE': 0.9968007592696619,
 '2mwvg7EagvMa7 tf book MAE': 0.9019144855016129,
 '2mwvg7EagvMa7 tf book MAPE ': 29.781183712933757,
 '2mwvg7EagvMa7 tf book Recall@K': 0.7962962962962963

In [91]:
evaldict.to_csv('./data/tf_eval.csv')

AttributeError: 'dict' object has no attribute 'to_csv'

In [ ]:
for i,user in enumerate(users):
    try:
        print(i,user)
        for model in models:
            rec_book=user_pref(user,model)
            rats=[]
            vc=[]
            avg_rt=[]
            for i in range(len(rec_book)):
                book = rec_book.index[i]
                rat = get_ans(user,book)
                vote= get_vtcnt(book)
                avg_rating=get_avg_rt(book)
                rats.append(rat)
                vc.append(vote)
                avg_rt.append(avg_rating)
            rec_book['user_rating']=rats
            rec_book['vote_count']=vc
            rec_book['avg_rating']=avg_rt

            rec_book=rec_book.fillna(0)
            user_3 = user_pref_book(user,3)
            recall_m=len(user_3)
            percentile=0.9
            m=rec_book['vote_count'].quantile(percentile)
            C=rec_book['avg_rating'].mean()
            rec_book['pred']=rec_book.apply(weight,axis=1)
            rec_book=rec_book.fillna(0)
            #사용자 평점 있는 책
            user_rec=rec_book[rec_book['user_rating']>0]
            min_rec=min(user_rec['user_rating'].values)
            y=user_rec['user_rating']
            pred=user_rec['pred']
            #user가 3점 이상 준 모든 책
            user_3 = user_pref_book(user,3)

            y=user_rec['user_rating']
            pred=user_rec['pred']
            user_like=len(rec_book[rec_book['user_rating']>3.5])
            recal=user_like/recall_m
            prek=user_like/len(user_rec)
            y=user_rec['user_rating']
            pred=user_rec['pred']
            user_like=len(rec_book[rec_book['user_rating']>3.5])
            recal=user_like/recall_m
            prek=user_like/len(user_rec)

            evaldict[user+' '+model+' '+'cross'+' '+'RMSE']=rmse(y,pred)

            evaldict[user+' '+model+' '+'cross'+' ''MAE']=mae(y,pred)

            evaldict[user+' '+model+' '+'cross'+' ''MAPE ']=mape(y,pred)

            evaldict[user+' '+model+' '+'cross'+' ''Recall@K'] = recal

            evaldict[user+' '+model+' '+'cross'+' ''Precision@K']=prek


            ####책
            bbyb= user_pref_b(user,model)
            bbyb=book_fc(bbyb)
            bbyb=bbyb.fillna(0)


            percentile=0.6
            m=bbyb['vote_count'].quantile(percentile)
            C=bbyb['avg_rating'].mean()
            bbyb['pred']=bbyb.apply(weight,axis=1)
            user_rec_b=bbyb[bbyb['user_rating']>0]
            y=user_rec_b['user_rating']
            pred=user_rec_b['pred']
            user_like=len(user_rec_b)
            recal=user_like/recall_m
            prek=user_like/len(bbyb)


            evaldict[user+' '+model+' '+'book'+' '+'RMSE']=rmse(y,pred)

            evaldict[user+' '+model+' '+'book'+' '+'MAE']=mae(y,pred)

            evaldict[user+' '+model+' '+'book'+' '+'MAPE ']=mape(y,pred)

            evaldict[user+' '+model+' '+'book'+' '+'Recall@K'] = recal

            evaldict[user+' '+model+' '+'book'+' '+'Precision@K']=prek
    except:
        print(i,user,'excpet')
        pass


0 2mwvgbGLgqMa7
m셰이프 오브 뮤직: 알렉상드르 데스플라
b노인을 위한 나라는 없다
b조제와 호랑이와 물고기들
b바깥은 여름
b라프 코스터의 재미이론
b남아 있는 나날
b한 달 후, 일 년 후
b태초에 사랑이 있었다
b7년의 밤
b호랑이를 덫에 가두면
b재미의 경계
b아내가 결혼했다
b죽은 시인의 사회
b콜 미 바이 유어 네임
b바둑 두는 여자
b독고솜에게 반하면
m인셉션
b영화를 찍으며 생각한 것
b바보 만들기
b뒷모습
b아몬드
b채식주의자
b공산당 선언
b방금 떠나온 세계
b알래스카, 바람 같은 이야기
b공산당선언
b인생
b소설처럼
b타인의 고통
b동물농장
b2020 제11회 젊은작가상 수상작품집
b인연
m쇼생크 탈출
b포
b좀머 씨 이야기
b중용
b파이트 클럽
b경성기담
b시민의 불복종
b방드르디, 태평양의 끝
b우리들의 행복한 시간
b속죄
b13계단
b강의
b질투
b가시고기
b미드나잇 라이브러리
b걸리버 여행기
m이터널 선샤인
b별들의 들판
b그러나 나는 살아가리라
b인간의 대지
b갈라파고스
b엄마가 사라졌다
b매디슨 카운티의 다리
b환상의 책
b미드나잇 라이브러리
b은비령
b모리와 함께한 화요일
b라프 코스터의 재미이론
b입 속의 검은 잎
b브리다
b귀뚜라미가 온다
b좀머 씨 이야기
m인생은 아름다워
b번쩍하는 황홀한 순간
b위대한 유산
b살아온 기적 살아갈 기적
b환상의 책
b타오르는 마음
b연애 소설 읽는 노인
b인형의 집
b불안한 사람들
b팩토텀
b퍼레이드
b얘들아, 너희가 나쁜 게 아니야
b인간의 대지
b기다림
b동백꽃
b커튼
m메멘토
b금각사
b자유로부터의 도피
b밤이여, 나뉘어라
b얘들아, 너희가 나쁜 게 아니야
b아프리카인
b책상은 책상이다
b건투를 빈다
b생명이 있는 것은 다 아름답다
b꿈의 해석
b검찰관
b죽음의 수용소에서
b투명인간
b역사란 무엇인가
b군주론
b혁명의 시대
m트루먼 쇼
b곽재구의 포구기행
b모렐의 발명
b싯다르타
b설득
b달려라, 아비
b인 콜드 블러드
b달의 궁전
b책상은 책상이다
b인생
b체 게바라 평

b시민의 불복종
b태초에 사랑이 있었다
b타인의 얼굴
b픽션들
b빙점
b당신 인생의 이야기
b소송
b입 속의 검은 잎
b모데라토 칸타빌레
b어린 왕자
b1984
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

...

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람
b내게 무해한 사람

In [ ]:
evaldict

In [632]:
users[4:]

Index(['2mwvgLpo25Ma7', '2mwvgYmarxMa7', '36lvX3jzZqXdn', '36lvXmWQZ5Xdn',
       '3BnvwpKaj5PAY', '3BnvwZ6bZqPAY', '4WLxZaDz65roA', '4WLxZaXN75roA',
       '4WLxZB8nkxroA', '4WLxZKgdmqroA',
       ...
       'YMKqmLrErxloD', 'YMKqmne6Pkvlo', 'YMKqmwrVr5loD', 'ZBm5Rgkl9xd46',
       'ZBm5RNnk95d46', 'ZBm5RVn735d46', 'zNM5N1gz7v26j', 'zNM5NARwPGv26',
       'ZWpqMaWa1qrkn', 'ZWpqMMERlqrkn'],
      dtype='object', length=106)

In [115]:
model

'tf'

In [116]:
for i,user in enumerate(users):
    try:
        print(i,user)
        rec_book = user_pref_ctt(user,tf)
        rats=[]
        vc=[]
        avg_rt=[]
        for i in range(len(rec_book)):
            book = rec_book.index[i]
            rat = get_ans(user,book)
            vote= get_vtcnt(book)
            avg_rating=get_avg_rt(book)
            rats.append(rat)
            vc.append(vote)
            avg_rt.append(avg_rating)
        rec_book['user_rating']=rats
        rec_book['vote_count']=vc
        rec_book['avg_rating']=avg_rt

        rec_book=rec_book.fillna(0)
        user_3 = user_pref_book(user,3)
        recall_m=len(user_3)
        percentile=0.9
        m=rec_book['vote_count'].quantile(percentile)
        C=rec_book['avg_rating'].mean()
        rec_book['pred']=rec_book.apply(weight,axis=1)
        rec_book=rec_book.fillna(0)
        #사용자 평점 있는 책
        user_rec=rec_book[rec_book['user_rating']>0]
        # min_rec=min(user_rec['user_rating'].values)
        if len(user_rec) == 0:
            evaldict[user+' '+model+' '+'onlyctt'+' '+'RMSE']=0
            evaldict[user+' '+model+' '+'onlyctt'+' '+'MAE']=0
            evaldict[user+' '+model+' '+'onlyctt'+' '+'MAPE ']=0
            evaldict[user+' '+model+' '+'onlyctt'+' '+'Recall@K'] = 0
            evaldict[user+' '+model+' '+'onlyctt'+' '+'Precision@K']=0
        else:
            y=user_rec['user_rating']
            pred=user_rec['pred']
            #user가 3점 이상 준 모든 책
            user_3 = user_pref_book(user,3)

            y=user_rec['user_rating']
            pred=user_rec['pred']
            user_like=len(rec_book[rec_book['user_rating']>3.5])
            recal=user_like/recall_m
            prek=user_like/len(user_rec)
            evaldict[user+' '+model+' '+'onlyctt'+' '+'RMSE']=rmse(y,pred)

            evaldict[user+' '+model+' '+'onlyctt'+' '+'MAE']=mae(y,pred)

            evaldict[user+' '+model+' '+'onlyctt'+' '+'MAPE ']=mape(y,pred)

            evaldict[user+' '+model+' '+'onlyctt'+' '+'Recall@K'] = recal
            evaldict[user+' '+model+' '+'onlyctt'+' '+'Precision@K']=prek
    except:
        print(i,user,'excpet')
        pass

0 24BqEWE785rjn
0 24BqEWE785rjn excpet
1 2mwvg7EagvMa7
1 2mwvg7EagvMa7 excpet
2 2mwvgaAjwxMa7
2 2mwvgaAjwxMa7 excpet
3 2mwvgbGLgqMa7
3 2mwvgbGLgqMa7 excpet
4 2mwvggAE2vMa7
4 2mwvggAE2vMa7 excpet
5 2mwvgLpo25Ma7
5 2mwvgLpo25Ma7 excpet
6 2mwvgYmarxMa7
6 2mwvgYmarxMa7 excpet
7 36lvX3jzZqXdn
7 36lvX3jzZqXdn excpet
8 36lvXmWQZ5Xdn
8 36lvXmWQZ5Xdn excpet
9 3BnvwpKaj5PAY
9 3BnvwpKaj5PAY excpet
10 3BnvwZ6bZqPAY
10 3BnvwZ6bZqPAY excpet
11 4WLxZaDz65roA
11 4WLxZaDz65roA excpet
12 4WLxZaXN75roA
12 4WLxZaXN75roA excpet
13 4WLxZB8nkxroA
13 4WLxZB8nkxroA excpet
14 4WLxZKgdmqroA
14 4WLxZKgdmqroA excpet
15 4WLxZmblW5roA
15 4WLxZmblW5roA excpet
16 4WLxZZ3wkxroA
16 4WLxZZ3wkxroA excpet
17 4WLxZZ7D8xroA
17 4WLxZZ7D8xroA excpet
18 6ADvG0XPK5zZl
18 6ADvG0XPK5zZl excpet
19 6ADvGZ98eqzZl
19 6ADvGZ98eqzZl excpet
20 6ewxaPbAwO5Q1
20 6ewxaPbAwO5Q1 excpet
21 6NW5Qb02wx1Yo
21 6NW5Qb02wx1Yo excpet
22 6NW5QB9Lyx1Yo
22 6NW5QB9Lyx1Yo excpet
23 6NW5QBDzwx1Yo
23 6NW5QBDzwx1Yo excpet
24 6NW5QzzJkx1Yo
24 6NW5QzzJkx1Yo ex

In [117]:
evaldict

{'ZWpqMaWa1qrkn tf onlyctt RMSE': 0,
 'ZWpqMaWa1qrkn tf onlyctt MAE': 0,
 'ZWpqMaWa1qrkn tf onlyctt MAPE ': 0,
 'ZWpqMaWa1qrkn tf onlyctt Recall@K': 0,
 'ZWpqMaWa1qrkn tf onlyctt Precision@K': 0}